In [64]:
import os
import pandas as pd

data_df = pd.DataFrame(columns=['text','Intent'])
filenames = list()
intervention_subgraphs = list()
for directory, subdirectories, files in os.walk('C:/Users/Tamir/Desktop/HSE_Project/excel_files/'):
    for file in files:
        filenames.append(os.path.join(directory,file))
for filename in filenames:
    if (filename[len(filename) - 22] == '~'):
        continue
    filename = filename.replace(" ", " ")
    post_df = pd.read_excel(filename)
    
        #fix to add columns if they are not in the xlsx file
    if 'attachments' not in post_df.columns:
        post_df['attachments'] = ''
    if 'reply_to_comment' not in post_df.columns:
        post_df['reply_to_comment'] = 0
    if 'reply_to_user' not in post_df.columns:
        post_df['reply_to_user'] = 0
        
    flex_df = post_df.drop(columns=['attachments','date','from_id','id','reply_to_comment','reply_to_user','Content','Intervention'])
    data_df = data_df.append(flex_df,ignore_index = True)

In [65]:
from nltk.corpus import stopwords
from nltk.tokenize import RegexpTokenizer
from nltk.stem.snowball import SnowballStemmer
tokenizer = RegexpTokenizer(r'\w+')
import pymorphy2

morph = pymorphy2.MorphAnalyzer()

def clean_text(text, remove_stopwords=True):
    """
    Removes stop words from the given text
    :param text: string with the text
    :param remove_stopwords: flag to enable removal of stop words
    :return: set of tokens without any stop words
    """
    text = text.lower()
    tokens = tokenizer.tokenize(text)
    tags = list()
    

    # Optionally, remove stop words
    if remove_stopwords:
        stops = set(stopwords.words('russian'))
        tokens = [w for w in tokens if w not in stops]
    for i in range(len(tokens)):
        tokens[i] = morph.parse(tokens[i])[0].normal_form
        t = morph.parse(tokens[i])[0]
        tokens[i] = tokens[i] + '_' + str(t.tag.POS)
    return tokens

delete_index = list()

for index,row in data_df.iterrows():
    if ( pd.isnull(data_df['text'].loc[index]) or pd.isnull(data_df['Intent'].loc[index]) 
              or (data_df['Intent'].loc[index] == ' -' ) ):
        delete_index.append(index)        
    else:
        data_df['text'].loc[index] = clean_text(data_df['text'].loc[index])

data_df = data_df.drop(index = delete_index)
data_df = data_df.reset_index(drop=True)

for index,row in data_df.iterrows():
    data_df['Intent'].loc[index] = data_df['Intent'].loc[index][0]
    if(data_df['Intent'].loc[index] == 'E'):
        print('change in ' + str(index))
        data_df['Intent'].loc[index] = 'Е'
        

            

change in 3158


In [66]:
#import json
#pymorphy_tags={
#        +'NOUN',  # имя существительное
#        +'ADJF',  # имя прилагательное (полное)
#        +'ADJS',  # имя прилагательное (краткое)
#        +'VERB',  # глагол (личная форма)
#        +'INFN',  # глагол (инфинитив)
#        +'PRTF',  # причастие (полное)
#        +'PRTS',  # причастие (краткое)
#        +'GRND',  # деепричастие
#        +'NUMR',  # числительное
#        +'ADVB',  # наречие
#        +'NPRO',  # местоимение-существительное
#        +'PRED',  # предикатив
#        +'PREP',  # предлог
#        +'CONJ',  # союз
#        +'PRCL',  # частица
#        +'INTJ',  # междометие
#}
#universal_tags={
#    +#ADJ: adjective
#    +#ADP: adposition
#    +#ADV: adverb
#    +#CCONJ: coordinating conjunction
#    +#DET: determiner
#    +#INTJ: interjection
#    +#NOUN: noun
#    +#NUM: numeral
#    +#PART: particle
#    +#PRON: pronoun
#    +#VERB: verb
#}

#Dict for tranformation pymorphy2 tags into universal POS tags

transform_dict = {'NOUN':'NOUN',
                  'ADJF':'ADJ',
                  'ADJS':'ADJ',
                  'PREP':'ADP',
                  'ADVB':'ADV',
                  'VERB':'VERB',
                  'INFN':'VERB',
                  'CONJ':'CCONJ',
                  'NPRO':'PRON',
                  'INTJ':'INTJ',
                  'PRCL':'PART',
                  'NUMR':'NUM',
                  'PRTF':'ADJ',
                  'PRTS':'ADJ',
                  'GRND':'ADJ',
                  'PRED':'ADJ'}

for index,row in data_df.iterrows():
    delete_list = list()
    print('new comment')
    comment = data_df['text'].loc[index]
    for i in range(len(comment) - 1):
        print('word: ' + comment[i])
        tag = comment[i].split('_')[len(comment[i].split('_'))-1]

        print('old tag: ' + tag)
        if (tag == 'None'):
            delete_list.append(comment[i])
        else:
            tag = transform_dict.get(tag)
            print('new tag: ' + tag)
            comment[i] = comment[i].split('_')[0] + '_' + tag
    for delete_value in delete_list:
        comment.remove(delete_value)



new comment
word: ага_INTJ
old tag: INTJ
new tag: INTJ
word: держать_INFN
old tag: INFN
new tag: VERB
word: карман_NOUN
old tag: NOUN
new tag: NOUN
new comment
word: id41764449_None
old tag: None
word: али_CONJ
old tag: CONJ
new tag: CCONJ
word: вариант_NOUN
old tag: NOUN
new tag: NOUN
word: улететь_INFN
old tag: INFN
new tag: VERB
word: венера_NOUN
old tag: NOUN
new tag: NOUN
word: фиговый_ADJF
old tag: ADJF
new tag: ADJ
new comment
word: пациент_NOUN
old tag: NOUN
new tag: NOUN
word: либо_CONJ
old tag: CONJ
new tag: CCONJ
word: живой_NOUN
old tag: NOUN
new tag: NOUN
word: либо_CONJ
old tag: CONJ
new tag: CCONJ
word: мёртвый_NOUN
old tag: NOUN
new tag: NOUN
word: буратино_NOUN
old tag: NOUN
new tag: NOUN
word: читать_INFN
old tag: INFN
new tag: VERB
new comment
word: id176345518_None
old tag: None
word: валерий_NOUN
old tag: NOUN
new tag: NOUN
word: это_PRCL
old tag: PRCL
new tag: PART
word: аналитика_NOUN
old tag: NOUN
new tag: NOUN
word: чей_ADJF
old tag: ADJF
new tag: ADJ
word: реа

word: иго_NOUN
old tag: NOUN
new tag: NOUN
word: сирия_NOUN
old tag: NOUN
new tag: NOUN
word: везде_ADVB
old tag: ADVB
new tag: ADV
word: тот_ADJF
old tag: ADJF
new tag: ADJ
word: край_NOUN
old tag: NOUN
new tag: NOUN
word: европа_NOUN
old tag: NOUN
new tag: NOUN
word: корень_NOUN
old tag: NOUN
new tag: NOUN
word: пустить_INFN
old tag: INFN
new tag: VERB
word: уничтожить_INFN
old tag: INFN
new tag: VERB
word: выбить_INFN
old tag: INFN
new tag: VERB
word: сирия_NOUN
old tag: NOUN
new tag: NOUN
word: думать_INFN
old tag: INFN
new tag: VERB
word: неа_None
old tag: None
word: быть_INFN
old tag: INFN
new tag: VERB
word: постоянно_ADVB
old tag: ADVB
new tag: ADV
word: возвращаться_INFN
old tag: INFN
new tag: VERB
word: благо_CONJ
old tag: CONJ
new tag: CCONJ
word: откуда_ADVB
old tag: ADVB
new tag: ADV
word: ливия_NOUN
old tag: NOUN
new tag: NOUN
word: египет_NOUN
old tag: NOUN
new tag: NOUN
word: ирак_NOUN
old tag: NOUN
new tag: NOUN
word: йемен_NOUN
old tag: NOUN
new tag: NOUN
word: турция

new tag: NOUN
word: заселить_INFN
old tag: INFN
new tag: VERB
word: давать_INFN
old tag: INFN
new tag: VERB
word: её_ADJF
old tag: ADJF
new tag: ADJ
word: кома_NOUN
old tag: NOUN
new tag: NOUN
word: нить_NOUN
old tag: NOUN
new tag: NOUN
word: сплавить_INFN
old tag: INFN
new tag: VERB
word: это_PRCL
old tag: PRCL
new tag: PART
word: полюбить_INFN
old tag: INFN
new tag: VERB
word: костянин_NOUN
old tag: NOUN
new tag: NOUN
word: видимо_ADVB
old tag: ADVB
new tag: ADV
word: тот_ADJF
old tag: ADJF
new tag: ADJ
word: который_ADJF
old tag: ADJF
new tag: ADJ
word: ям_NOUN
old tag: NOUN
new tag: NOUN
word: ходить_INFN
old tag: INFN
new tag: VERB
word: жить_INFN
old tag: INFN
new tag: VERB
word: это_PRCL
old tag: PRCL
new tag: PART
word: проблема_NOUN
old tag: NOUN
new tag: NOUN
word: государство_NOUN
old tag: NOUN
new tag: NOUN
word: срать_NOUN
old tag: NOUN
new tag: NOUN
word: ям_NOUN
old tag: NOUN
new tag: NOUN
word: жить_INFN
old tag: INFN
new tag: VERB
word: человечески_ADVB
old tag: ADVB
n

new tag: ADV
word: один_ADJF
old tag: ADJF
new tag: ADJ
new comment
word: задолбать_INFN
old tag: INFN
new tag: VERB
word: вообще_ADVB
old tag: ADVB
new tag: ADV
word: африка_NOUN
old tag: NOUN
new tag: NOUN
word: выйти_INFN
old tag: INFN
new tag: VERB
new comment
word: промыть_INFN
old tag: INFN
new tag: VERB
word: мозги_NOUN
old tag: NOUN
new tag: NOUN
word: иметь_INFN
old tag: INFN
new tag: VERB
word: свойство_NOUN
old tag: NOUN
new tag: NOUN
word: обрастать_INFN
old tag: INFN
new tag: VERB
word: новый_ADJF
old tag: ADJF
new tag: ADJ
word: наслоение_NOUN
old tag: NOUN
new tag: NOUN
word: чудо_NOUN
old tag: NOUN
new tag: NOUN
word: человек_NOUN
old tag: NOUN
new tag: NOUN
new comment
word: украина_NOUN
old tag: NOUN
new tag: NOUN
word: скорее_CONJ
old tag: CONJ
new tag: CCONJ
word: потерять_INFN
old tag: INFN
new tag: VERB
word: остаться_INFN
old tag: INFN
new tag: VERB
word: существовать_INFN
old tag: INFN
new tag: VERB
word: тот_ADJF
old tag: ADJF
new tag: ADJ
word: политик_NOUN
ol

old tag: NOUN
new tag: NOUN
word: блин_INTJ
old tag: INTJ
new tag: INTJ
word: тот_ADJF
old tag: ADJF
new tag: ADJ
word: автоколонна_NOUN
old tag: NOUN
new tag: NOUN
word: построить_INFN
old tag: INFN
new tag: VERB
word: авианосец_NOUN
old tag: NOUN
new tag: NOUN
word: 10_None
old tag: None
word: ярд_NOUN
old tag: NOUN
new tag: NOUN
word: ага_INTJ
old tag: INTJ
new tag: INTJ
word: слепой_ADJF
old tag: ADJF
new tag: ADJ
word: везде_ADVB
old tag: ADVB
new tag: ADV
word: отвечать_INFN
old tag: INFN
new tag: VERB
word: мы_NPRO
old tag: NPRO
new tag: PRON
new comment
word: id218379731_None
old tag: None
word: аким_NOUN
old tag: NOUN
new tag: NOUN
word: мы_NPRO
old tag: NPRO
new tag: PRON
word: выгода_NOUN
old tag: NOUN
new tag: NOUN
word: слить_INFN
old tag: INFN
new tag: VERB
word: каддафи_NOUN
old tag: NOUN
new tag: NOUN
word: прокакать_INFN
old tag: INFN
new tag: VERB
word: деньга_NOUN
old tag: NOUN
new tag: NOUN
word: полтора_NUMR
old tag: NUMR
new tag: NUM
word: авианосец_NOUN
old tag: 

...

old tag: INFN
new tag: VERB
word: сам_ADJF
old tag: ADJF
new tag: ADJ
word: пора_NOUN
old tag: NOUN
new tag: NOUN
word: делать_INFN
old tag: INFN
new tag: VERB
word: пытаться_INFN
old tag: INFN
new tag: VERB
word: улучшить_INFN
old tag: INFN
new tag: VERB
word: жизнь_NOUN
old tag: NOUN
new tag: NOUN
word: шизик_NOUN
old tag: NOUN
new tag: NOUN
word: подсунуть_INFN
old tag: INFN
new tag: VERB
word: враг_NOUN
old tag: NOUN
new tag: NOUN
word: видеть_INFN
old tag: INFN
new tag: VERB
word: 90_None
old tag: None
word: человек_NOUN
old tag: NOUN
new tag: NOUN
word: жить_INFN
old tag: INFN
new tag: VERB
word: запад_NOUN
old tag: NOUN
new tag: NOUN
word: вообще_ADVB
old tag: ADVB
new tag: ADV
word: никакой_ADJF
old tag: ADJF
new tag: ADJ
word: дело_NOUN
old tag: NOUN
new tag: NOUN
word: россия_NOUN
old tag: NOUN
new tag: NOUN
word: складываться_INFN
old tag: INFN
new tag: VERB
word: впечатление_NOUN
old tag: NOUN
new tag: NOUN
word: 90_None
old tag: None
word: население_NOUN
old tag: NOUN
new 

word: ещё_ADVB
old tag: ADVB
new tag: ADV
word: наплакаться_INFN
old tag: INFN
new tag: VERB
new comment
word: патриотический_ADJF
old tag: ADJF
new tag: ADJ
word: лагерь_NOUN
old tag: NOUN
new tag: NOUN
word: это_PRCL
old tag: PRCL
new tag: PART
word: хороший_ADJF
old tag: ADJF
new tag: ADJ
word: идея_NOUN
old tag: NOUN
new tag: NOUN
word: говорить_INFN
old tag: INFN
new tag: VERB
word: здоровый_ADJF
old tag: ADJF
new tag: ADJ
word: патриотизм_NOUN
old tag: NOUN
new tag: NOUN
word: учить_INFN
old tag: INFN
new tag: VERB
word: любить_INFN
old tag: INFN
new tag: VERB
word: родина_NOUN
old tag: NOUN
new tag: NOUN
word: поддерживать_INFN
old tag: INFN
new tag: VERB
word: хороший_ADJF
old tag: ADJF
new tag: ADJ
word: человеческий_ADJF
old tag: ADJF
new tag: ADJ
word: качество_NOUN
old tag: NOUN
new tag: NOUN
word: заниматься_INFN
old tag: INFN
new tag: VERB
word: спорт_NOUN
old tag: NOUN
new tag: NOUN
word: забывать_INFN
old tag: INFN
new tag: VERB
new comment
word: id209776161_None
old ta

old tag: NOUN
new tag: NOUN
word: рельефный_ADJF
old tag: ADJF
new tag: ADJ
word: мозг_NOUN
old tag: NOUN
new tag: NOUN
word: говорить_INFN
old tag: INFN
new tag: VERB
word: согласиться_INFN
old tag: INFN
new tag: VERB
word: самый_ADJF
old tag: ADJF
new tag: ADJ
word: сексуальный_ADJF
old tag: ADJF
new tag: ADJ
word: часть_NOUN
old tag: NOUN
new tag: NOUN
word: тело_NOUN
old tag: NOUN
new tag: NOUN
word: мужчина_NOUN
old tag: NOUN
new tag: NOUN
new comment
word: id350530155_None
old tag: None
word: виктор_NOUN
old tag: NOUN
new tag: NOUN
word: человек_NOUN
old tag: NOUN
new tag: NOUN
word: должный_ADJF
old tag: ADJF
new tag: ADJ
word: тупой_ADJF
old tag: ADJF
new tag: ADJ
new comment
word: id2799963_None
old tag: None
word: алексей_NOUN
old tag: NOUN
new tag: NOUN
word: это_PRCL
old tag: PRCL
new tag: PART
word: наличие_NOUN
old tag: NOUN
new tag: NOUN
word: бумажка_NOUN
old tag: NOUN
new tag: NOUN
word: показывать_INFN
old tag: INFN
new tag: VERB
new comment
word: id350530155_None
old

word: заголовок_NOUN
old tag: NOUN
new tag: NOUN
word: ничто_NPRO
old tag: NPRO
new tag: PRON
word: конкретный_ADJF
old tag: ADJF
new tag: ADJ
new comment
word: возможно_CONJ
old tag: CONJ
new tag: CCONJ
new comment
word: f35_None
old tag: None
word: f22_None
old tag: None
new comment
new comment
word: скандальный_ADJF
old tag: ADJF
new tag: ADJ
word: заголовок_NOUN
old tag: NOUN
new tag: NOUN
word: статья_NOUN
old tag: NOUN
new tag: NOUN
word: похоже_CONJ
old tag: CONJ
new tag: CCONJ
word: автор_NOUN
old tag: NOUN
new tag: NOUN
word: отписаться_INFN
old tag: INFN
new tag: VERB
word: ради_PREP
old tag: PREP
new tag: ADP
new comment
word: просто_PRCL
old tag: PRCL
new tag: PART
word: новый_ADJF
old tag: ADJF
new tag: ADJ
word: большой_ADJF
old tag: ADJF
new tag: ADJ
word: дорогой_ADVB
old tag: ADVB
new tag: ADV
word: тачка_NOUN
old tag: NOUN
new tag: NOUN
word: современный_ADJF
old tag: ADJF
new tag: ADJ
new comment
word: он_NPRO
old tag: NPRO
new tag: PRON
word: полетать_INFN
old tag: 

old tag: ADJF
new tag: ADJ
word: дорога_NOUN
old tag: NOUN
new tag: NOUN
new comment
word: чтожий_ADJF
old tag: ADJF
new tag: ADJ
word: салоеда_NOUN
old tag: NOUN
new tag: NOUN
word: такой_ADJF
old tag: ADJF
new tag: ADJ
word: пиз_None
old tag: None
word: лы_None
old tag: None
word: стать_INFN
old tag: INFN
new tag: VERB
word: лишь_PRCL
old tag: PRCL
new tag: PART
word: чушь_NOUN
old tag: NOUN
new tag: NOUN
word: нести_INFN
old tag: INFN
new tag: VERB
word: какой_ADJF
old tag: ADJF
new tag: ADJ
word: очко_NOUN
old tag: NOUN
new tag: NOUN
word: амерекос_NOUN
old tag: NOUN
new tag: NOUN
new comment
word: id20007107_None
old tag: None
new comment
word: ть_None
old tag: None
word: почему_ADVB
old tag: ADVB
new tag: ADV
word: люба_NOUN
old tag: NOUN
new tag: NOUN
word: топика_NOUN
old tag: NOUN
new tag: NOUN
word: итог_NOUN
old tag: NOUN
new tag: NOUN
word: сводиться_INFN
old tag: INFN
new tag: VERB
word: украина_NOUN
old tag: NOUN
new tag: NOUN
word: срач_NOUN
old tag: NOUN
new tag: NOUN
w

In [69]:
def create_average_vec(doc, vec_dim, ft_model):
    average = np.zeros((vec_dim,), dtype='float32')
    num_words = 0.
    for word in doc:
        if word in ft_model.wv.vocab:
            average = np.add(average, ft_model[word])
            num_words += 1.
    if num_words != 0.:
        average = np.divide(average, num_words)
    return average

word_counter = 0
model_counter = 0
for index,row in data_df.iterrows():
    comment = data_df['text'].loc[index]
    for word in comment:
        word_counter += 1
        if (word in model.vocab):
            model_counter += 1
print('All the words in data after preprocessing: ' + str(word_counter))
print('Words in model vacabulary: ' + str(model_counter))

All the words in data after preprocessing: 47792
Words in model vacabulary: 36163


In [80]:
import numpy as np
vector_data = list()


for index,row in data_df.iterrows(): 
    comment = data_df['text'].loc[index]
    comment_vector = np.zeros((300,), dtype='float32')
    words = 0
    for word in comment:
        if (word in model.vocab):
            comment_vector = np.add(comment_vector,model[word])
            words += 1
    if (words != 0):
        comment_vector = np.divide(comment_vector,words)
    vector_data.append(comment_vector)

In [59]:
import gensim
import codecs
from gensim.models.wrappers import FastText
import gensim.downloader as api

#FastText.load_model('cc.ru.300')
model = api.load("word2vec-ruscorpora-300")

#w2v_file = codecs.open('cc.ru.300.bin.gz', encoding='utf-8')
#model = gensim.models.KeyedVectors.load_word2vec_format(w2v_file, binary=True)  # or binary=False if the model is not compressed

KeyboardInterrupt: 

In [95]:
import numpy as np
np.random.seed(123)  # for reproducibility
 
from keras.models import Sequential
from keras.layers import Dense, Dropout, Activation, Flatten
from keras.layers import Convolution1D, MaxPooling1D
from keras.utils import np_utils
from keras.datasets import mnist
from sklearn.model_selection import train_test_split

label_list = list()
for intent in data_df['Intent']:
    label_list.append(intent)

# 4. Load pre-shuffled MNIST data into train and test sets
X_train, X_test, y_train, y_test = train_test_split(vector_data, label_list, test_size=0.2, random_state = 42, stratify = label_list)

 
# 5. Preprocess input data
#X_train = X_train.reshape(X_train.shape[0], 1, 28, 28)
#X_test = X_test.reshape(X_test.shape[0], 1, 28, 28)
#X_train = X_train.astype('float32')
#X_test = X_test.astype('float32')
#X_train /= 255
#X_test /= 255
 
# 6. Preprocess class labels
Y_train = np_utils.to_categorical(y_train, 25)
Y_test = np_utils.to_categorical(y_test, 25)
 
# 7. Define model architecture
model = Sequential()
 
model.add(Conv1D(128, 5, activation='relu'))
model.add(MaxPooling1D(5))
model.add(Conv1D(128, 5, activation='relu'))
model.add(MaxPooling1D(5))
model.add(Conv1D(128, 5, activation='relu'))
model.add(GlobalMaxPooling1D())
model.add(Dense(128, activation='relu'))
model.add(Dense(25, activation='softmax'))
          

 
# 8. Compile model
model.compile(loss='categorical_crossentropy',
              optimizer='rmsprop',
              metrics=['acc'])
          
# 9. Fit model on training data
model.fit(X_train, Y_train, 
          batch_size=32, nb_epoch=10, verbose=1)
 
# 10. Evaluate model on test data
score = model.evaluate(X_test, Y_test, verbose=0)

ValueError: invalid literal for int() with base 10: 'Н'

In [70]:
tags = list()
for word in model.vocab:
    print(word)

весь_DET
человек_NOUN
мочь_VERB
год_NOUN
сказать_VERB
время_NOUN
говорить_VERB
становиться_VERB
знать_VERB
самый_DET
дело_NOUN
день_NOUN
жизнь_NOUN
рука_NOUN
очень_ADV
первый_ADJ
давать_VERB
новый_ADJ
слово_NOUN
иметь_VERB
большой_ADJ
идти_VERB
глаз_NOUN
место_NOUN
лицо_NOUN
видеть_VERB
хотеть_VERB
понимать_VERB
должный_ADJ
работа_NOUN
каждый_DET
друг_NOUN
голова_NOUN
дом_NOUN
оставаться_VERB
сторона_NOUN
начинать_VERB
думать_VERB
хорошо_ADV
жить_VERB
стоять_VERB
спрашивать_VERB
сделать_VERB
выходить_VERB
последний_ADJ
русский_ADJ
сила_NOUN
получать_VERB
какой-то_DET
хороший_ADJ
случай_NOUN
вопрос_NOUN
отвечать_VERB
россия_NOUN
несколько_NUM
мир_NOUN
город_NOUN
делать_VERB
пойти_VERB
приходить_VERB
земля_NOUN
принимать_VERB
часть_NOUN
вид_NOUN
ребенок_NOUN
конец_NOUN
взять_VERB
всякий_DET
находить_VERB
высокий_ADJ
сидеть_VERB
что-то_PRON
отец_NOUN
оказываться_VERB
вода_NOUN
смотреть_VERB
москва_NOUN
час_NOUN
являться_VERB
народ_NOUN
любить_VERB
проходить_VERB
никто_PRON
образ_NOUN
каза

соглашение_NOUN
свободно_ADV
одинокий_ADJ
конструкция_NOUN
управлять_VERB
супруга_NOUN
сигнал_NOUN
свадьба_NOUN
плыть_VERB
местность_NOUN
др_NOUN
горький_ADJ
объединять_VERB
лампа_NOUN
таинственный_ADJ
девка_NOUN
монах_NOUN
япония_NOUN
жесткий_ADJ
трудность_NOUN
забор_NOUN
замуж_ADV
волноваться_VERB
красавица_NOUN
воздействие_NOUN
вор_NOUN
сопротивление_NOUN
пассажир_NOUN
школьный_ADJ
воспринимать_VERB
волга_NOUN
помещик_NOUN
подушка_NOUN
подхватывать_VERB
поцеловать_VERB
выигрывать_VERB
слабость_NOUN
замечание_NOUN
рис_NOUN
дедушка_NOUN
отражать_VERB
ужасно_ADV
радио_NOUN
излагать_VERB
оправдывать_VERB
единство_NOUN
опираться_VERB
испугаться_VERB
гнев_NOUN
ой_INTJ
украшать_VERB
информационный_ADJ
ступать_VERB
общение_NOUN
суровый_ADJ
прокурор_NOUN
удовлетворять_VERB
последующий_ADJ
владеть_VERB
кризис_NOUN
коля_NOUN
нуждаться_VERB
столетие_NOUN
психологический_ADJ
окружающий_ADJ
ильич_NOUN
подводить_VERB
грозный_ADJ
николаевна_NOUN
подождать_VERB
жалкий_ADJ
проявление_NOUN
орден_NOUN


погодить_VERB
помиловать_VERB
треть_NOUN
вскричать_VERB
отравлять_VERB
кучер_NOUN
гул_NOUN
запевать_VERB
регистрация_NOUN
стремительно_ADV
хранение_NOUN
людской_ADJ
сашка_NOUN
освещение_NOUN
хан_NOUN
взвод_NOUN
хребет_NOUN
африка_NOUN
нью-йорк_NOUN
вот-вот_ADV
принципиальный_ADJ
мчаться_VERB
преступный_ADJ
миссия_NOUN
общаться_VERB
выживать_VERB
сени_NOUN
протекать_VERB
мыслить_VERB
познавать_VERB
град_NOUN
школьник_NOUN
маркс_NOUN
оператор_NOUN
бумажный_ADJ
увезти_VERB
бред_NOUN
ограниченный_ADJ
калитка_NOUN
загораться_VERB
кора_NOUN
дворянский_ADJ
квадратный_ADJ
сельскохозяйственный_ADJ
интервью_NOUN
половой_ADJ
семьдесят_NUM
роскошь_NOUN
размышлять_VERB
содействие_NOUN
возражение_NOUN
оперативный_ADJ
стон_NOUN
шепнуть_VERB
замерзать_VERB
самгин_NOUN
спирт_NOUN
плащ_NOUN
поставка_NOUN
симпатия_NOUN
ноготь_NOUN
уважаемый_ADJ
прохор_NOUN
связываться_VERB
мутный_ADJ
отель_NOUN
неправда_NOUN
начальный_ADJ
скучать_VERB
цирк_NOUN
улетать_VERB
пробыть_VERB
шевелиться_VERB
филипп_NOUN
устойч

руководящий_ADJ
подвигаться_VERB
прыгнуть_VERB
икра_NOUN
фрагмент_NOUN
наедине_ADV
распределять_VERB
превосходство_NOUN
наименование_NOUN
намереваться_VERB
внучка_NOUN
сформировывать_VERB
розыск_NOUN
убогий_ADJ
засовывать_VERB
надвигаться_VERB
зловещий_ADJ
запираться_VERB
жутко_ADV
варя_NOUN
братский_ADJ
излучение_NOUN
поверхностный_ADJ
нищий_ADJ
воспроизводить_VERB
поплыть_VERB
футбол_NOUN
обнажать_VERB
навоз_NOUN
башмак_NOUN
бригадир_NOUN
регулярный_ADJ
форум_NOUN
тяга_NOUN
параллельно_ADV
ноздря_NOUN
проповедовать_VERB
пополам_ADV
крутиться_VERB
завет_NOUN
затея_NOUN
арестованный_NOUN
менеджер_NOUN
смирнов_NOUN
тонуть_VERB
ужинать_VERB
представительство_NOUN
штурм_NOUN
блин_NOUN
четырнадцать_NUM
спешивать_VERB
архитектурный_ADJ
отбывать_VERB
унижать_VERB
баран_NOUN
борец_NOUN
оживленный_ADJ
плотность_NOUN
деление_NOUN
корпорация_NOUN
доброволец_NOUN
вцепляться_VERB
софия_NOUN
львович_NOUN
корма_NOUN
выпрямляться_VERB
липа_NOUN
перекрещиваться_VERB
караван_NOUN
усиленный_ADJ
защитный

булгаков_NOUN
мечтательный_ADJ
секретарша_NOUN
роды_NOUN
отливать_VERB
пятеро_NUM
зеленоватый_ADJ
питие_NOUN
хозяйский_ADJ
волчий_ADJ
выяснение_NOUN
пятерка_NOUN
орда_NOUN
монгольский_ADJ
щелкать_VERB
подкреплять_VERB
ребеночек_NOUN
житься_VERB
справлять_VERB
вежливость_NOUN
королевство_NOUN
необъяснимый_ADJ
издержки_NOUN
привычно_ADV
поить_VERB
приглядываться_VERB
эдакий_DET
расхохотаться_VERB
топот_NOUN
интеллект_NOUN
дивиться_VERB
послевоенный_ADJ
подслушивать_VERB
горесть_NOUN
насос_NOUN
голодать_VERB
нервничать_VERB
идол_NOUN
разгадывать_VERB
погибель_NOUN
противиться_VERB
кадровый_ADJ
затруднительный_ADJ
поползти_VERB
коротенький_ADJ
лира_NOUN
код_NOUN
зараза_NOUN
двинуть_VERB
неудобство_NOUN
рассеянно_ADV
кудрявый_ADJ
неловкий_ADJ
пошлость_NOUN
вступаться_VERB
явственно_ADV
привязываться_VERB
противоречивый_ADJ
балл_NOUN
пересмотр_NOUN
ввп_NOUN
змей_NOUN
нквд_NOUN
му_NOUN
таракан_NOUN
пеший_ADJ
рождать_VERB
оборонительный_ADJ
ориентировать_VERB
сандро_NOUN
уютно_ADV
епархия_NOUN

...

поимка_NOUN
верка_NOUN
штурвал_NOUN
невпопад_ADV
фрунзе_NOUN
упразднение_NOUN
отключаться_VERB
одиссея_NOUN
бабель_NOUN
увещевать_VERB
творчески_ADV
спецназ_NOUN
навязнуть_VERB
подаяние_NOUN
упрятывать_VERB
язычество_NOUN
суслов_NOUN
бесноваться_VERB
челябинск_NOUN
передок_NOUN
засаленный_ADJ
чик_NOUN
словосочетание_NOUN
пакт_NOUN
кадыров_NOUN
смельчак_NOUN
кусаться_VERB
нейрон_NOUN
несвоевременный_ADJ
омерзение_NOUN
биохимический_ADJ
несостоятельный_ADJ
журавлев_NOUN
ухоженный_ADJ
ирод_NOUN
родоначальник_NOUN
стариковский_ADJ
латышский_ADJ
упущение_NOUN
мурлыкать_VERB
папский_ADJ
хватиться_VERB
четырехлетний_ADJ
съедобный_ADJ
кап_NOUN
загромождать_VERB
продувать_VERB
посадник_NOUN
заводчик_NOUN
проходимец_NOUN
шумахер_NOUN
нараспев_ADV
серго_NOUN
слепить_VERB
слуцкий_NOUN
ядовито_ADV
иерей_NOUN
бескорыстно_ADV
полицеймейстер_NOUN
дымчатый_ADJ
копченый_ADJ
завхоз_NOUN
подтекст_NOUN
подмастерье_NOUN
моллюск_NOUN
целенаправленный_ADJ
мемориальный_ADJ
сморкаться_VERB
зонд_NOUN
чихать_VERB

хлесткий_ADJ
святилище_NOUN
смокинг_NOUN
антип_NOUN
преходить_VERB
корректировать_VERB
долговечный_ADJ
зверски_ADV
слизь_NOUN
цепко_ADV
ракитин_NOUN
предводительство_NOUN
нагрудный_ADJ
затопать_VERB
остервенение_NOUN
козаков_NOUN
der_NOUN
фигурный_ADJ
тезка_NOUN
ат_NOUN
бережок_NOUN
постесняться_VERB
добегать_VERB
внутренно_ADV
тормозной_ADJ
календарный_ADJ
марья::гавриловна_NOUN
любимая_NOUN
пластырь_NOUN
трагичный_ADJ
царедворец_NOUN
разгребать_VERB
набрасывать_VERB
трлн_NOUN
петровка_NOUN
разносчик_NOUN
скривиться_VERB
перевоз_NOUN
григорьич_NOUN
мазут_NOUN
задвижка_NOUN
вольдемар_NOUN
стройно_ADV
универмаг_NOUN
колдунья_NOUN
натуга_NOUN
скворец_NOUN
курень_NOUN
яровой_ADJ
лувр_NOUN
собственноручный_ADJ
смотрение_NOUN
квадратик_NOUN
проверенный_ADJ
чепчик_NOUN
пещерный_ADJ
сомов_NOUN
окачивать_VERB
ст::гпк_NOUN
шельма_NOUN
ита_NOUN
егерский_ADJ
испарина_NOUN
вершить_VERB
обложение_NOUN
лексика_NOUN
буйвол_NOUN
зарываться_VERB
докучаев_NOUN
ягодица_NOUN
тор_NOUN
изабелла_NOUN
общенар

агрессор_NOUN
низводить_VERB
запальчивый_ADJ
корениться_VERB
вспухать_VERB
весельчак_NOUN
селекция_NOUN
неузнаваемость_NOUN
вялость_NOUN
гадюка_NOUN
кукурузный_ADJ
забастовать_VERB
ло_NOUN
нефтепровод_NOUN
аввакум_NOUN
загривок_NOUN
сконфуженно_ADV
самооборона_NOUN
коротышка_NOUN
новобрачный_NOUN
тверской::бульвар_NOUN
гоготать_VERB
вареник_NOUN
предтеча_NOUN
калифорнийский_ADJ
пахота_NOUN
сгорбленный_ADJ
потеснить_VERB
брест_NOUN
застройщик_NOUN
долговечность_NOUN
впопыхах_ADV
прорубать_VERB
руал_NOUN
сгубить_VERB
респектабельный_ADJ
палаш_NOUN
паз_NOUN
шоссейный_ADJ
кокарда_NOUN
апогей_NOUN
снос_NOUN
засесть_VERB
тургеневский_ADJ
околоточный_NOUN
пономарь_NOUN
каркать_VERB
лепта_NOUN
платежный_ADJ
нач_NOUN
простительный_ADJ
базиль_NOUN
красногвардеец_NOUN
зашибать_VERB
градский_ADJ
заколебаться_VERB
единожды_ADV
наборщик_NOUN
зловонный_ADJ
застаиваться_VERB
убиенный_ADJ
напускной_ADJ
зеленин_NOUN
михайловский_ADJ
своевольный_ADJ
резаться_VERB
четвероногий_ADJ
але_INTJ
маркушка_NOUN
з

затравливать_VERB
нюрочка_NOUN
мвф_NOUN
багажный_ADJ
кошечка_NOUN
босу_ADV
улизнуть_VERB
неспешный_ADJ
одноразовый_ADJ
бранный_ADJ
кисея_NOUN
ареал_NOUN
обезопасить_VERB
бейлиса_NOUN
вегетативный_ADJ
импульсный_ADJ
кандидатский_ADJ
колоритный_ADJ
цой_NOUN
мужеский_ADJ
портик_NOUN
сачок_NOUN
скок_NOUN
грезиться_VERB
конический_ADJ
тронутый_ADJ
телекоммуникационный_ADJ
милосердый_ADJ
торс_NOUN
восточнее_ADV
разгульный_ADJ
вышагивать_VERB
поколотить_VERB
переполняться_VERB
просверливать_VERB
заслушиваться_VERB
женни_NOUN
зудеть_VERB
пирс_NOUN
вспугивать_VERB
перепуг_NOUN
душечка_NOUN
бездыханный_ADJ
напитывать_VERB
километровый_ADJ
восемнадцатилетний_ADJ
вакса_NOUN
цедить_VERB
преподаваться_VERB
барбара_NOUN
атлантический_ADJ
чудово_NOUN
популяризация_NOUN
обшлаг_NOUN
подгруппа_NOUN
опочивальня_NOUN
гу_NOUN
насылать_VERB
раздосадовать_VERB
анжела_NOUN
претить_VERB
трехкомнатный_ADJ
баловень_NOUN
уч_NOUN
замуровывать_VERB
ротный_NOUN
обувной_ADJ
безводный_ADJ
горошина_NOUN
ингредиент_NOUN


KeyboardInterrupt: 

In [43]:
tokens = ['ага','держи','карман','шире']
for i in range(len(tokens)):
    print(tokens[i])
    tokens[i] = morph.parse(tokens[i])[0].normal_form
    t = morph.parse(tokens[i])[0]
    tokens[i] = tokens[i] + '_' + str(t.tag.POS)
    print(tokens[i])
print(tokens)


tokens = ['ага','держи','карман','шире']
for token in tokens:
    print(token)
    token = morph.parse(token)[0].normal_form
    t = morph.parse(token)[0]
    token = token+'_'+str(t.tag.POS)
    print(token)
print(tokens)

ага
ага_INTJ
держи
держать_INFN
карман
карман_NOUN
шире
шире_NOUN
['ага_INTJ', 'держать_INFN', 'карман_NOUN', 'шире_NOUN']
ага
ага_INTJ
держи
держать_INFN
карман
карман_NOUN
шире
шире_NOUN
['ага', 'держи', 'карман', 'шире']


In [1]:
import pymorphy2
morph = pymorphy2.MorphAnalyzer()

word = 'дома'
word = morph.parse(word)[0].normal_form
t = morph.parse(word)[0]
word = word+'_'+str(t.tag.POS)

In [84]:
len(vector_data)

3661

In [91]:
data_df['Intent'].unique()

array(['Ц', 'Н', 'Ш', 'Ж', 'И', 'Ч', 'Т', 'Щ', 'А', 'Г', 'У', 'Х', 'Б',
       'Д', 'Л', 'В', 'Е', 'П', 'К', 'С', 'М', 'Ф', 'З', 'Р', 'О'],
      dtype=object)

In [37]:
!pip install pymorphy2

  Running setup.py bdist_wheel for docopt: started
  Running setup.py bdist_wheel for docopt: finished with status 'done'
  Stored in directory: C:\Users\Tamir\AppData\Local\pip\Cache\wheels\9b\04\dd\7daf4150b6d9b12949298737de9431a324d4b797ffd63f526e
Successfully built docopt


notebook 5.4.0 requires ipykernel, which is not installed.
jupyter 1.0.0 requires ipykernel, which is not installed.
jupyter-console 5.2.0 requires ipykernel, which is not installed.
ipywidgets 7.1.1 requires ipykernel>=4.5.1, which is not installed.
distributed 1.20.2 requires msgpack-python, which is not installed.
tensorflow 1.11.0 has requirement setuptools<=39.1.0, but you'll have setuptools 40.4.3 which is incompatible.
pyowm 2.8.0 has requirement requests<2.19,>=2.18.2, but you'll have requests 2.19.1 which is incompatible.
copydoc 1.0.9 has requirement beautifulsoup4==4.4.1, but you'll have beautifulsoup4 4.6.3 which is incompatible.
You are using pip version 10.0.1, however version 18.1 is available.
You should consider upgrading via the 'python -m pip install --upgrade pip' command.
